# Tutorial: Approximate Global Text Explanation (AGTE) - IMDb movie review sentiment rules explanation
Explaining an IMDb Movie Reviews Text Classification Tensorflow Model globally for a dataset with Approximate Global Text Explanation via linear models. his is a global explanation procedure in which the effects of all input data points are analyzed. AGTE uses the approach of ALTE for this and extends it with an N-fold execution. Accordingly, several linear models are trained which represent the original classification function at different points. The more data points exist and the more computational capacity is available (i.e. the more permutations can be calculated and classified), the better the approximation of the original model. In addition, a pipeline is implemented, with the help of which the effect representation (token and its effect on certain classes) can be converted into a decision rule set (DecisionTree).

### 1. Imports and Configuration
For the original classification model we use TensorFlow, for the dataset and its transformation TensorFlow Dataset and Pandas Dataframe, for mathemathical operations Numpy and text processing RegEx and String libraries.

In [1]:
import re
import string
import tensorflow as tf
import tensorflow_datasets as tfds
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib

from tensorflow.python.keras import Sequential
from tensorflow.python.keras.layers import Embedding, Dropout, GlobalAveragePooling1D, Dense
from tensorflow.python.keras.losses import BinaryCrossentropy
from tensorflow.python.keras.metrics import BinaryAccuracy
from sklearn import tree
from ate.base import AGTE, ATE_Options

Configuration by TensorFlow tutorial "Basic Text Classification":
- MAX_FEATURES = Vocabulary size
- EMBEDDING_DIM = Token embedding vector size
- SEQUENCE_LENGTH = Max. tokens for classification
- BATCH_SIZE = Dataset batching size
- AUTOTUNE = Buffer size

In [2]:
MAX_FEATURES = 10000
EMBEDDING_DIM = 16
SEQUENCE_LENGTH = 250
BATCH_SIZE = 32
AUTOTUNE = tf.data.AUTOTUNE

### 2. Loading and Preparation
Initial downloading of IMDb movie review dataset by usind TensorFlow Dataset.

In [3]:
raw_train_ds = tfds.load('imdb_reviews', split='train').batch(BATCH_SIZE)
raw_test_ds = tfds.load('imdb_reviews', split='test').batch(BATCH_SIZE)

Metal device set to: Apple M1 Pro


2023-03-25 15:05:10.807473: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:305] Could not identify NUMA node of platform GPU ID 0, defaulting to 0. Your kernel may not have been built with NUMA support.
2023-03-25 15:05:10.807556: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:271] Created TensorFlow device (/job:localhost/replica:0/task:0/device:GPU:0 with 0 MB memory) -> physical PluggableDevice (device: 0, name: METAL, pci bus id: <undefined>)


Using a **custom standardization** function to process the textual data and stripping html tags and punctuation.

In [4]:
def custom_standardization(input_data):
    lowercase = tf.strings.lower(input_data)
    stripped_html = tf.strings.regex_replace(lowercase, '<br />', ' ')
    return tf.strings.regex_replace(stripped_html, '[%s]' % re.escape(string.punctuation), '')

**Vectorization** of the textual data by using a vocabulary and transforming the tokens into integer ids (id vectors).

In [5]:
vectorize_layer = tf.keras.layers.TextVectorization(
    standardize=custom_standardization,
    max_tokens=MAX_FEATURES,
    output_mode='int',
    output_sequence_length=SEQUENCE_LENGTH)

In [6]:
train_text = raw_train_ds.map(lambda x: x['text'])
vectorize_layer.adapt(train_text)

2023-03-25 15:05:10.954247: W tensorflow/core/platform/profile_utils/cpu_utils.cc:128] Failed to get CPU frequency: 0 Hz
2023-03-25 15:05:10.999242: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:113] Plugin optimizer for device_type GPU is enabled.


In [7]:
def vectorize_text(text, label):
    text = tf.expand_dims(text, -1)
    return vectorize_layer(text), label

In [8]:
train_ds = raw_train_ds.map(lambda x: vectorize_text(x['text'], x['label']))
test_ds = raw_test_ds.map(lambda x: vectorize_text(x['text'], x['label']))

In [9]:
train_ds = train_ds.cache().prefetch(buffer_size=AUTOTUNE)
test_ds = test_ds.cache().prefetch(buffer_size=AUTOTUNE)

### 3. Creating and Training
Creation and trainig of the classification model.

In [10]:
embedding_layer = Embedding(MAX_FEATURES + 1, EMBEDDING_DIM)
model = Sequential([
    embedding_layer,
    Dropout(0.2),
    GlobalAveragePooling1D(),
    Dropout(0.2),
    Dense(1)
])

In [11]:
model.compile(loss=BinaryCrossentropy(from_logits=True),
              optimizer='adam',
              metrics=BinaryAccuracy(threshold=0.0))

In [12]:
history = model.fit(train_ds, epochs=5)

Epoch 1/5


2023-03-25 15:05:12.935499: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:113] Plugin optimizer for device_type GPU is enabled.


782/782 [==============================] - 14s 18ms/step - loss: 0.6495 - binary_accuracy: 0.7083
Epoch 2/5
782/782 [==============================] - 10s 13ms/step - loss: 0.5021 - binary_accuracy: 0.8220
Epoch 3/5
782/782 [==============================] - 9s 12ms/step - loss: 0.3943 - binary_accuracy: 0.8633
Epoch 4/5
782/782 [==============================] - 9s 12ms/step - loss: 0.3319 - binary_accuracy: 0.8826
Epoch 5/5
782/782 [==============================] - 9s 12ms/step - loss: 0.2905 - binary_accuracy: 0.8970


In [13]:
loss, accuracy = model.evaluate(test_ds)

print("Loss: ", loss)
print("Accuracy: ", accuracy)

  6/782 [..............................] - ETA: 8s - loss: 0.3753 - binary_accuracy: 0.8125  

2023-03-25 15:06:04.831138: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:113] Plugin optimizer for device_type GPU is enabled.


782/782 [==============================] - 4s 4ms/step - loss: 0.3371 - binary_accuracy: 0.8638
Loss:  0.3371306359767914
Accuracy:  0.8638400435447693


### 4. Explaining
Initializing AGTE by providing the Tokinization, Vectorization , Classification Function. Additionaly initializing the ATE_Options with the column names, permutation (approximation) steps, permutation border (per step), classes (1 for binary; >2 for multi-class/-label), linear epochs. 

In [14]:
embeddings = embedding_layer.get_weights()[0]
ids_list = vectorize_layer.get_vocabulary()
ids = dict(zip(ids_list, range(len(ids_list))))

In [15]:
def standardization(x):
    x = x.lower()
    x = re.sub('<br />', ' ', x)
    return re.sub('[%s]' % re.escape(string.punctuation), '', x)
def tokenize(x):
    return np.array(x.lower().split())
def vectorize(x):
    if not x in ids:
        return [0]*EMBEDDING_DIM
    token_id = ids[standardization(x)]
    embedding_vec = embeddings[token_id]
    return embedding_vec
def classify(x):
    id_vecs = []
    for e in x['text'].tolist():
        id_vec = vectorize_layer(' '.join(e)).numpy().tolist()
        if len(id_vec) == 0:
            id_vec = [0]*SEQUENCE_LENGTH
        id_vecs.append(id_vec)
    return model.predict(id_vecs)
ate = AGTE(
    tokenize,
    vectorize,
    classify,
)
options = ATE_Options(['text'], 4, 500, 1, 10)

In [16]:
test_df = tfds.as_dataframe(raw_test_ds).head(25)
test_df = pd.DataFrame([i['text'][0].decode('UTF-8') for _, i in test_df.iterrows()], columns=['text'])
effects, bow = ate.transform_effects(ate.explain(test_df, options))

0it [00:00, ?it/s]2023-03-25 15:06:09.593395: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:113] Plugin optimizer for device_type GPU is enabled.


Epoch 1/10


2023-03-25 15:06:09.873738: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:113] Plugin optimizer for device_type GPU is enabled.


5/5 [==============================] - 1s 57ms/step - loss: 0.1806 - accuracy: 0.4969
Epoch 2/10
5/5 [==============================] - 0s 18ms/step - loss: 0.1773 - accuracy: 0.5094
Epoch 3/10
5/5 [==============================] - 0s 10ms/step - loss: 0.1734 - accuracy: 0.5220
Epoch 4/10
5/5 [==============================] - 0s 7ms/step - loss: 0.1702 - accuracy: 0.5346
Epoch 5/10
5/5 [==============================] - 0s 7ms/step - loss: 0.1680 - accuracy: 0.5660
Epoch 6/10
5/5 [==============================] - 0s 22ms/step - loss: 0.1658 - accuracy: 0.5660
Epoch 7/10
5/5 [==============================] - 0s 14ms/step - loss: 0.1639 - accuracy: 0.5723
Epoch 8/10
5/5 [==============================] - 0s 7ms/step - loss: 0.1620 - accuracy: 0.5786
Epoch 9/10
5/5 [==============================] - 0s 7ms/step - loss: 0.1602 - accuracy: 0.6164
Epoch 10/10
5/5 [==============================] - 0s 7ms/step - loss: 0.1585 - accuracy: 0.6226
Epoch 1/10
16/16 [===========================


1it [00:17, 17.37s/it]

...


24it [07:51, 19.30s/it]

Epoch 1/10


2023-03-25 15:14:00.853103: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:113] Plugin optimizer for device_type GPU is enabled.


4/4 [==============================] - 1s 152ms/step - loss: 0.1389 - accuracy: 0.4783
Epoch 2/10
4/4 [==============================] - 0s 26ms/step - loss: 0.1234 - accuracy: 0.4783
Epoch 3/10
4/4 [==============================] - 0s 15ms/step - loss: 0.0986 - accuracy: 0.4783
Epoch 4/10
4/4 [==============================] - 0s 16ms/step - loss: 0.0781 - accuracy: 0.4870
Epoch 5/10
4/4 [==============================] - 0s 7ms/step - loss: 0.0525 - accuracy: 0.4870
Epoch 6/10
4/4 [==============================] - 0s 8ms/step - loss: 0.0358 - accuracy: 0.4870
Epoch 7/10
4/4 [==============================] - 0s 7ms/step - loss: 0.0086 - accuracy: 0.4870
Epoch 8/10
4/4 [==============================] - 0s 39ms/step - loss: -0.0164 - accuracy: 0.4870
Epoch 9/10
4/4 [==============================] - 0s 7ms/step - loss: -0.0342 - accuracy: 0.4870
Epoch 10/10
4/4 [==============================] - 0s 17ms/step - loss: -0.0607 - accuracy: 0.4870
Epoch 1/10
16/16 [======================

25it [08:08, 19.55s/it]
100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 6492/6492 [00:00<00:00, 1158896.05it/s]
6492it [00:00, 556725.04it/s]


In [17]:
effects_df = pd.DataFrame(effects, columns=['token', 'effect'])
effects_df['effect'] = effects_df['effect'].apply(lambda x: 1 if x[0] > 0.5 else -1 if x[0] < -0.5 else 0)

In [18]:
effects_df

token  effect
0     [1.0, 0.602934773230848, -0.7817480642958479, ...       0
1     [0.602934773230848, 1.0000000000000002, -0.441...       0
2     [-0.7817480642958479, -0.44154932155841814, 1....       0
3     [0.11928511348435344, 0.22093922850024714, 0.0...       0
4     [0.9793781022851963, 0.6229247311830117, -0.72...       0
...                                                 ...     ...
6487  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...       0
6488  [-0.9658302458613416, -0.6115731134700251, 0.7...       1
6489  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...       0
6490  [-0.9720679154041529, -0.6616300487479946, 0.7...       0
6491  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...       0

[6492 rows x 2 columns]

In [19]:
clf = tree.DecisionTreeClassifier()
clf = clf.fit(effects_df['token'].tolist(), effects_df['effect'].tolist())

In [21]:
plt.figure(figsize=(200,200))
tree.plot_tree(clf, feature_names=list(bow.keys()), fontsize=10)
plt.show()